In [2]:
#!pip install avalanche-lib==0.3.1
#!pip install torcheval
#!pip install numba
!pip install numpy==1.23

Looking in indexes: https://pypi.org/simple, https://packagecloud.io/github/git-lfs/pypi/simple
Using cached numpy-1.23.0-cp39-cp39-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (17.1 MB)
  Attempting uninstall: numpy
    Found existing installation: numpy 1.21.0
    Uninstalling numpy-1.21.0:
      Successfully uninstalled numpy-1.21.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
daal4py 2021.6.0 requires daal==2021.4.0, which is not installed.
numba 0.55.1 requires numpy<1.22,>=1.18, but you have numpy 1.23.0 which is incompatible.
torchtext 0.10.1 requires torch==1.9.1, but you have torch 1.12.1+cu113 which is incompatible.

[notice] A new release of pip is available: 23.3.2 -> 24.0
[notice] To update, run: pip install --upgrade pip


# Imports

In [1]:
from itertools import product
from itertools import combinations

from avalanche.benchmarks.classic import SplitMNIST
from avalanche.benchmarks.generators import dataset_benchmark


import torch
import torchvision
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
from torch.utils.tensorboard import SummaryWriter



import torch.nn.functional as F
from torcheval.metrics.functional import multiclass_confusion_matrix
from torch.optim import Adam
from torch.nn import CrossEntropyLoss

from torchvision.utils import save_image
from torchvision.transforms import ToTensor
from torchvision.datasets import ImageFolder
from torchvision import transforms


#from AE import TransformerAE


from itertools import product
from itertools import combinations


import matplotlib.pyplot as plt 
import seaborn as sns
from matplotlib.animation import FuncAnimation ,FFMpegWriter ,PillowWriter

import dill
import numpy as np
import os
import json
import pandas as pd
from tqdm import tqdm
import copy

In [2]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
device

device(type='cuda', index=0)

### Data creation

In [ ]:
for k in range(10):
    if not(os.path.isdir(".//data//SplitMnist//train//")):
        os.mkdir(".//data//SplitMnist//train//")
    if not(os.path.isdir(".//data//SplitMnist//train//{}".format(k))):
        os.mkdir(".//data//SplitMnist//train//{}".format(k))
    if not(os.path.isdir(".//data//SplitMnist//test//")):
        os.mkdir(".//data//SplitMnist//test//")
    if not(os.path.isdir(".//data//SplitMnist//test//{}".format(k))):
        os.mkdir(".//data//SplitMnist//test//{}".format(k))
for i in tqdm(range(len(split_mnist.train_stream))):
    for j in range(len(split_mnist.train_stream[i].dataset)):
        save_image(split_mnist.train_stream[i].dataset[j][0], ".//data//SplitMnist//train//{}//{}.png".format(split_mnist.train_stream[i].dataset[j][1],j))
    #print("fold {}//{}//{}.png saved".format(j,L_labels1[img_idx],test_index[img_idx]))

In [ ]:
for i in tqdm(range(len(split_mnist.test_stream))):
    for j in range(len(split_mnist.test_stream[i].dataset)):
        save_image(split_mnist.test_stream[i].dataset[j][0], ".//data//SplitMnist//test//{}//{}.png".format(split_mnist.test_stream[i].dataset[j][1],j))

In [3]:
from torchvision import datasets
IMG_EXTENSIONS = ('.jpg', '.jpeg', '.png', '.ppm', '.bmp', '.pgm', '.tif', '.tiff', '.webp')

class ClassSpecificImageFolder(datasets.DatasetFolder):
    def __init__(
            self,
            root,
            dropped_classes=[],
            transform = None,
            target_transform = None,
            loader = datasets.folder.default_loader,
            is_valid_file = None,
    ):
        self.dropped_classes = dropped_classes
        super(ClassSpecificImageFolder, self).__init__(root, loader, IMG_EXTENSIONS if is_valid_file is None else None,
                                                       transform=transform,
                                                       target_transform=target_transform,
                                                       is_valid_file=is_valid_file)
        self.imgs = self.samples

    def find_classes(self, directory):
        classes = sorted(entry.name for entry in os.scandir(directory) if entry.is_dir())
        classes = [c for c in classes if c not in self.dropped_classes]
        if not classes:
            raise FileNotFoundError(f"Couldn't find any class folder in {directory}.")

        class_to_idx = {cls_name: i for i, cls_name in enumerate(classes)}
        return classes, class_to_idx

# Combinations

## Single experiences

In [4]:
#ListExperiences=list()
ListExperiences_=list()
All=list(range(10))
for sample in range(2,10,1):
    S=combinations(range(10), sample)
    #All=list(range(10))
    for i in S :
        L1=list(i)
        L2=[k for k in All if k not in L1] 
        ListExperiences_.append(L1)
len(ListExperiences_)
ListExperiences_.append([x for x in range(10)])

In [5]:
ListExperiences_.append([x for x in range(10)])

## Pairs of experiences (with and without repetition)

In [6]:
Pairs_exp=list()

All=list(range(10))
for sample in range(2,9,1):
    S=combinations(range(10), sample)
    #All=list(range(10))
    for i in S :
        L1=list(i)
        L2=[k for k in All if k not in L1] 
        for sample2 in range(2,9,1):
            S2=combinations(L2, sample2)
            for j in S2:
                pair=[]
                pair.append(L1)
                sub=list(j)
                pair.append(sub)
                Pairs_exp.append(pair)
len(Pairs_exp)

46872

In [7]:
Pairs_exp=list()
All=list(range(10))
for sample in range(2,9,1):
    S=combinations(range(10), sample)
    #All=list(range(10))
    for i in S :
        L1=list(i)
        L2=[k for k in All if k not in L1] 
        for sample2 in range(2,9,1):
            S2=combinations(L2, sample2)
            for j in S2:
                pair=[]
                pair.append(L1)
                sub=list(j)
                pair.append(sub)
                pair.sort()
                if pair not in Pairs_exp :
                    Pairs_exp.append(pair)
len(Pairs_exp)             

23436

In [8]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")


class CNN(nn.Module):
    def __init__(
        self,
        channels_in,
        nlin="leakyrelu",
        dropout=0.0,
        init_type="uniform",
    ):
        super().__init__()
        # init module list
        self.module_list = nn.ModuleList()
        ### ASSUMES 28x28 image size
        ## compose layer 1
        self.module_list.append(nn.Conv2d(channels_in, 8, 5))
        self.module_list.append(nn.MaxPool2d(2, 2))
        self.module_list.append(self.get_nonlin(nlin))
        # apply dropout
        if dropout > 0:
            self.module_list.append(nn.Dropout(dropout))
        ## compose layer 2
        self.module_list.append(nn.Conv2d(8, 6, 5))
        self.module_list.append(nn.MaxPool2d(2, 2))
        self.module_list.append(self.get_nonlin(nlin))
        ## add dropout
        if dropout > 0:
            self.module_list.append(nn.Dropout(dropout))
        ## compose layer 3
        self.module_list.append(nn.Conv2d(6, 4, 2))
        self.module_list.append(self.get_nonlin(nlin))
        ## add flatten layer
        self.module_list.append(nn.Flatten())
        ## add linear layer 1
        self.module_list.append(nn.Linear(3 * 3 * 4, 20))
        self.module_list.append(self.get_nonlin(nlin))
        ## add dropout
        if dropout > 0:
            self.module_list.append(nn.Dropout(dropout))
        ## add linear layer 1
        self.module_list.append(nn.Linear(20, 10))

        ### initialize weights with se methods
        self.initialize_weights(init_type)

    def initialize_weights(self, init_type):
        # print("initialze model")
        for m in self.module_list:
            if type(m) == nn.Linear or type(m) == nn.Conv2d:
                if init_type == "xavier_uniform":
                    torch.nn.init.xavier_uniform_(m.weight)
                if init_type == "xavier_normal":
                    torch.nn.init.xavier_normal_(m.weight)
                if init_type == "uniform":
                    torch.nn.init.uniform_(m.weight)
                if init_type == "normal":
                    torch.nn.init.normal_(m.weight)
                if init_type == "kaiming_normal":
                    torch.nn.init.kaiming_normal_(m.weight)
                if init_type == "kaiming_uniform":
                    torch.nn.init.kaiming_uniform_(m.weight)
                # set bias to some small non-zero value
                m.bias.data.fill_(0.01)

    def get_nonlin(self, nlin):
        # apply nonlinearity
        if nlin == "leakyrelu":
            return nn.LeakyReLU()
        if nlin == "relu":
            return nn.ReLU()
        if nlin == "tanh":
            return nn.Tanh()
        if nlin == "sigmoid":
            return nn.Sigmoid()
        if nlin == "silu":
            return nn.SiLU()
        if nlin == "gelu":
            return nn.GELU()


    def forward(self, x):
        # forward prop through module_list
        for layer in self.module_list:
            x = layer(x)
        return x

    def forward_activations(self, x):
        # forward prop through module_list
        activations = []
        for layer in self.module_list:
            x = layer(x)
            if (
                isinstance(layer, nn.Tanh)
                or isinstance(layer, nn.Sigmoid)
                or isinstance(layer, nn.ReLU)
                or isinstance(layer, nn.LeakyReLU)
                or isinstance(layer, nn.SiLU)
                or isinstance(layer, nn.GELU)
                or isinstance(layer, ORU)
                or isinstance(layer, ERU)
            ):
                activations.append(x)
        return x, activations
def train(model, trainloader, optimizer, criterion,nb_classes):
    List_mx=[]
    model.train()
    #print('Training')
    train_running_loss = 0.0
    train_running_correct = 0
    counter = 0
    for i, data in enumerate(trainloader):
        counter += 1
        image, labels = data
        image = image.to(device)
        labels = labels.to(device)
        optimizer.zero_grad()
        # forward pass
        outputs = model(image)
        # calculate the loss
        loss = criterion(outputs, labels)
        train_running_loss += loss.item()
        # calculate the accuracy
        _, preds = torch.max(outputs.data, 1)
        train_running_correct += (preds == labels).sum().item()
        mx=multiclass_confusion_matrix(preds ,labels,nb_classes,normalize="pred")
        List_mx.append(mx)
        # backpropagation
        loss.backward()
        # update the optimizer parameters
        optimizer.step()
    
    # loss and accuracy for the complete epoch
    epoch_loss = train_running_loss / counter
    epoch_acc = 100. * (train_running_correct / len(trainloader.dataset))
    return epoch_loss, epoch_acc,List_mx


def validate(model, testloader, criterion,nb_classes):
    List_mx=[]
    model.eval()
    valid_running_loss = 0.0
    valid_running_correct = 0
    counter = 0
    with torch.no_grad():
        for i, data in enumerate(testloader):
            counter += 1
            
            image, labels = data
            image = image.to(device)
            labels = labels.to(device)
            # forward pass
            outputs = model(image)
            # calculate the loss
            loss = criterion(outputs, labels)
            valid_running_loss += loss.item()
            # calculate the accuracy
            _, preds = torch.max(outputs.data, 1)
            valid_running_correct += (preds == labels).sum().item()
            mx=multiclass_confusion_matrix(preds ,labels,nb_classes,normalize="pred")
            List_mx.append(mx)
        
    # loss and accuracy for the complete epoch
    epoch_loss = valid_running_loss / counter
    epoch_acc = 100. * (valid_running_correct / len(testloader.dataset))
    return epoch_loss, epoch_acc,List_mx
def create_frame(step,ax,data):
    ax=ax.cla()
    sns.heatmap(data[step][-1].cpu(),annot=True,cmap="cubehelix",ax=ax,cbar=False)
    plt.title('Epoch {} training {}'.format(step,exp)  )

In [9]:
#train_loaders_paths=[ "./data/SplitMnist/train/{}".format(x) for x in range(10)]
#test_loaders_paths=[ "./data/SplitMnist/test/{}".format(x) for x in range(10)]


torch.manual_seed(887)
L_activations=["leakyrelu"]#,"leakyrelu","sigmoid"]#,"relu","silu","tanh"]"tanh","sigmoid",
L_inits=["kaiming_uniform"]



All=list(range(10))
patience=3
Margin=0.05
for i in range(len(L_activations)):
    for t,exp in enumerate(L2_[-5:]):
        L_train_acc=[]
        L_train_loss=[]
        L_test_acc_0=[]
        L_test_loss_0=[]
        
        L2=[k for k in All if k not in exp] 
        train_IF=ClassSpecificImageFolder( root="./data/SplitMnist/train/",dropped_classes=L2,transform=transforms.Compose([ transforms.ToTensor(),transforms.Grayscale(1)]))
        T_DL = DataLoader(dataset=train_IF, batch_size=90, num_workers=0, shuffle=True)
        test_IF=ClassSpecificImageFolder( root="./data/SplitMnist/test/",dropped_classes=L2,transform=transforms.Compose([ transforms.ToTensor(),transforms.Grayscale(1)]))
        Ts_DL = DataLoader(dataset=train_IF, batch_size=90, num_workers=0, shuffle=True)

        model = CNN(1,L_activations[i],0,L_inits[0])
        if not(os.path.isdir('./checkpoints/')):
            os.mkdir('./checkpoints/')
        if not(os.path.isdir('./checkpoints/{}/'.format(exp))):
            os.mkdir('./checkpoints/{}/'.format(exp))
        if not(os.path.isdir('./checkpoints/{}/{}'.format(exp,L_activations[i]))):
            os.mkdir('./checkpoints/{}/{}'.format(exp,L_activations[i]))
        if not(os.path.isdir('./checkpoints/{}/{}/metrics/'.format(exp,L_activations[i]))):
            os.mkdir('./checkpoints/{}/{}/metrics/'.format(exp,L_activations[i]))


        # lists to keep track of losses and accuracies
        train_loss, valid_loss_0 = [], [] 
        train_acc, valid_acc_0 = [], []
        train_confus,test_confus =[] , []
        Brain=copy.deepcopy(model)
        Brain=Brain.to(device)

        optimizer = Adam(Brain.parameters(), lr=0.05)
        scheduler = torch.optim.lr_scheduler.CyclicLR(optimizer, base_lr=1e-3, max_lr=0.1, step_size_up=1, mode="triangular2", cycle_momentum=False)

        criterion = CrossEntropyLoss()

        valid_epoch_loss0, valid_epoch_acc0,L_mx_st = validate(Brain, Ts_DL,criterion,10)
        valid_loss_0.append(valid_epoch_loss0)
        valid_acc_0.append(valid_epoch_acc0)
        test_confus.append(L_mx_st)
        #print(f"Validation loss: {valid_epoch_loss0:.3f}, validation acc 1: {valid_epoch_acc0:.3f}")

        #print('-'*50)
        # start the training
        stagnate=0
        for epoch in range(41):
            print(f"[INFO]: Epoch {epoch+1} of 40" , t ,L_activations[i])
            train_epoch_loss, train_epoch_acc ,L_mx = train(Brain, T_DL, optimizer, criterion,10)
            train_confus.append(L_mx)
            train_loss.append(train_epoch_loss)
            train_acc.append(train_epoch_acc)
            valid_epoch_loss0, valid_epoch_acc0,L_mx= validate(Brain, Ts_DL,  criterion,10)
            test_confus.append(L_mx)
            valid_loss_0.append(valid_epoch_loss0)
            valid_acc_0.append(valid_epoch_acc0)
            print(f"Training loss: {train_epoch_loss:.3f}, training acc: {train_epoch_acc:.3f}")
            print(f"Validation loss: {valid_epoch_loss0:.3f}, validation acc 1: {valid_epoch_acc0:.3f}")

            if (valid_epoch_acc0 >60) and (epoch >= 9):
                if epoch %5==1:
                    torch.save({'epoch': aux,'model_state_dict': Brain.state_dict(),'optimizer_state_dict': optimizer.state_dict(),},'./checkpoints/{}/{}/checkpoint epoch {}.pth'.format(exp,L_activations[i],epoch))
                if (abs(valid_epoch_acc0-valid_acc_0[-2])<=Margin)  :
                    print("stagnation")
                    stagnate=stagnate+1
                    if stagnate==patience :
                        epoch=-1
                    else:
                        continue
                else:
                    stagnate=0
                aux=epoch
                if (epoch==-1) :
                    aux=epoch
                    break
            print('-'*50)


        #torch.save(Brain.state_dict(),'./checkpoints/{}/{}/{}/checkpoint.pth'.format(ListExperiences[exp_idx][:5],activ,init))
        if epoch==-1:
             torch.save({'epoch': aux,'model_state_dict': Brain.state_dict(),'optimizer_state_dict': optimizer.state_dict(),},'./checkpoints/{}/{}/checkpoint.pth'.format(exp,L_activations[i],epoch))
        else :
            torch.save({'epoch': aux,'model_state_dict': Brain.state_dict(),'optimizer_state_dict': optimizer.state_dict(),},'./checkpoints/{}/{}/checkpoint epoch {}.pth'.format(exp,L_activations[i],epoch))
        L_train_acc.append(train_acc)
        L_train_loss.append(train_loss)
        L_test_acc_0.append(valid_acc_0)
        L_test_loss_0.append(valid_loss_0)

        direct='./checkpoints/{}/{}/metrics/'.format(exp,L_activations[i])
        M=np.array(L_test_acc_0) 
        np.save(direct+"Test Accuracy IID.npy", M)

        H=np.array(L_test_loss_0)
        np.save(direct+"Test Loss IID.npy",H)


        N=np.array(L_train_acc)
        np.save(direct+"Train Acc.npy",N)

        O=np.array(L_train_loss)
        np.save(direct+"Train Loss.npy",O)
        
        P=[train_confus[i][-1].cpu() for i in range(len(train_confus))]
        P=torch.stack(P)
        P=np.transpose(P, (1, 2, 0))
        np.save(direct+"multiclass train Confusion matrix raw.npy",P)
        
        W=[test_confus[i][-1].cpu() for i in range(len(test_confus))]
        W=torch.stack(W)
        W=np.transpose(W, (1, 2, 0))
        np.save(direct+"multiclass test Confusion matrix raw.npy",W)
        
        fig, ax = plt.subplots() 
        ax.cla()
        animation = FuncAnimation(fig, create_frame, frames=len(train_confus), fargs=(ax,train_confus))
        wr=PillowWriter(fps=1)
        animation.save('./checkpoints/{}/{}/metrics/Training mcx.gif'.format(exp,L_activations[i]) , writer=wr)
        fig, ax = plt.subplots() 
        ax.cla()
        animation = FuncAnimation(fig, create_frame, frames=len(test_confus), fargs=(ax,test_confus))
        wr=PillowWriter(fps=1)
        animation.save('./checkpoints/{}/{}/metrics/Testing mcx.gif'.format(exp,L_activations[i]) , writer=wr)


NameError: name 'L2_' is not defined

### Access weights

In [16]:
ListModelvec=[]
check=torch.load(f".//checkpoints//{ListExperiences[exp][:5]}//{L_activations[activ]}//{L_inits[init]}//checkpoint.pth",pickle_module=dill,map_location=device)
model = CNN(1,activ,0,init)
model=model.to(device)
model.load_state_dict(check["model_state_dict"])
L_param=[]
for param in model.parameters():
    m = nn.Flatten(0,-1)
    L_param.append(m(param))
vec = torch.Tensor()
vec=vec.to(device)
for idx in L_param:
    vec = torch.cat((vec, idx.view(-1)))
print(vec.shape)
ListModelvec.append(vec)

NameError: name 'ListExperiences' is not defined

In [43]:
acc=np.load(f".//checkpoints//{ListExperiences[0]}//silu//metrics//Test Accuracy IID.npy")
acc[0][11+1]

98.29166666666667

In [20]:
acc[0][-1]

97.725

In [8]:
L_activations=["gelu","relu","silu","leakyrelu","sigmoid","tanh"]#,"relu","gelu","tanh"]
L_inits=["kaiming_uniform"]

Cols=["label"]+[x for x in range(10)]+["Activation"]+["weight {}".format(x) for x in range(200)]+["bias {}".format(x) for x in range(200,208)]+["weight {}".format(x) for x in range(208,1408)]+["bias {}".format(x) for x in range(1408,1414)]+["weight {}".format(x) for x in range(1414,1510)]+["bias {}".format(x) for x in range(1510,1514)]+["weight {}".format(x) for x in range(1514,2234)]+["bias {}".format(x) for x in range(2234,2254)]+["weight {}".format(x) for x in range(2254,2454)]+["bias {}".format(x) for x in range(2454,2464)]+["Accuracy"]
check_name=[' epoch 11',' epoch 16',' epoch 21',' epoch 26',' epoch 31',' epoch 36']
Weights= pd.DataFrame(columns=Cols)

All=list(range(10))
for activ in L_activations:
    for name in check_name:
        Weights= pd.DataFrame(columns=Cols)
        for exp in tqdm(ListExperiences_) :
            files=os.listdir(f".//checkpoints//{exp}//{activ}//")
            rest_names=[x for x in set(files)-set([f'checkpoint{y}.pth' for y in check_name])] 
            rest_names.remove('metrics')
            row=[]

            row.append(exp)
            for label in All:
                if label in exp:
                    row.append(1)
                else:
                    row.append(0)

            row.append(activ)
            try:
                check=torch.load(f".//checkpoints//{exp}//{activ}//checkpoint{name}.pth",pickle_module=dill,map_location=device)
            except:
                if len(rest_names)>1:
                    print("Multiple ending checkpoints")
                for auxi in rest_names:
                    check=torch.load(f".//checkpoints//{exp}//{activ}/{auxi}",pickle_module=dill,map_location=device)
                
            model = CNN(1,L_activations[0],0,L_inits[0])
            model=model.to(device)
            model.load_state_dict(check["model_state_dict"])
            L_param=[]
            for param in model.parameters():
                m = nn.Flatten(0,-1)
                L_param.append(m(param))
            vec = torch.Tensor()
            vec=vec.to(device)
            for idx in L_param:
                vec = torch.cat((vec, idx.view(-1)))
            vec=vec.detach().cpu().numpy()
            row.extend(vec)

            acc=np.load(f".//checkpoints//{exp}//{activ}//metrics//Test Accuracy IID.npy")
            if name != '' and int(name[-2:])<=len(acc[0]):
                row.append(acc[0][int(name[-2:])-1])
            else:
                row.append(acc[0][-1])
            Weights.loc[len(Weights)]=row

        print(Weights.head(2).style.set_properties(subset=['Activation'], **{'width': '300px'}))
        Weights.to_csv(f"Weights {activ}{name}.csv", index=False)

100%|██████████| 1013/1013 [01:58<00:00,  8.53it/s]


100%|██████████| 1013/1013 [01:57<00:00,  8.66it/s]


 98%|█████████▊| 996/1013 [01:56<00:02,  8.16it/s]

Multiple endinging checkpoints


100%|██████████| 1013/1013 [01:58<00:00,  8.57it/s]


...

 96%|█████████▌| 970/1013 [01:51<00:05,  8.36it/s]

Multiple endinging checkpoints


 96%|█████████▌| 975/1013 [01:52<00:04,  8.37it/s]

Multiple endinging checkpoints


100%|██████████| 1013/1013 [01:56<00:00,  8.68it/s]


### Create train , validation , test loaders 

In [80]:
df_sil=pd.read_csv("./data/Weights silu epoch 36.csv")
print(len(df_sil), df_sil['Accuracy'].mean())
param_columns=df_sil.columns[12:-1]
l=[0,1]
df_sil[df_sil['label']=='{}'.format([0,1])]

1013 98.78942415268189


label  0  1  2  3  4  5  6  7  8  ...  bias 2455 bias 2456  bias 2457  \
0  [0, 1]  1  1  0  0  0  0  0  0  0  ...   0.544951 -0.281758   0.025728   

   bias 2458  bias 2459  bias 2460  bias 2461  bias 2462  bias 2463   Accuracy  
0  -0.323952   0.448369   -0.02704   0.320681  -0.363458  -0.193887  98.948333  

[1 rows x 2477 columns]

In [81]:
df_gel=pd.read_csv("./data/Weights gelu epoch 36.csv")
print(len(df_gel) ,df_gel['Accuracy'].mean() )
param_columns=df_gel.columns[12:-1]
l=[0,1]
df_gel[df_gel['label']=='{}'.format([0,1])]

1013 98.72053471536681


label  0  1  2  3  4  5  6  7  8  ...  bias 2455 bias 2456  bias 2457  \
0  [0, 1]  1  1  0  0  0  0  0  0  0  ...   0.454077 -0.126967   -0.04321   

   bias 2458  bias 2459  bias 2460  bias 2461  bias 2462  bias 2463   Accuracy  
0  -0.231192   0.342562  -0.112175    0.27983   -0.13655  -0.327724  98.643333  

[1 rows x 2477 columns]

In [82]:
df_rel=pd.read_csv("./data/Weights relu epoch 36.csv")

print(len(df_rel) ,df_rel['Accuracy'].mean() )
l=[0,1]
df_rel[df_rel['label']=='{}'.format([0,1])]

1013 98.60784468575193


label  0  1  2  3  4  5  6  7  8  ...  bias 2455 bias 2456  bias 2457  \
0  [0, 1]  1  1  0  0  0  0  0  0  0  ...   0.652486 -0.199251  -0.131497   

   bias 2458  bias 2459  bias 2460  bias 2461  bias 2462  bias 2463   Accuracy  
0  -0.161827   0.185681   -0.07153   0.577306  -0.418235  -0.292624  98.821667  

[1 rows x 2477 columns]

In [83]:
df_sig=pd.read_csv("./data/Weights sigmoid epoch 36.csv")

print(len(df_sig) ,df_sig['Accuracy'].mean() )
l=[0,1]
df_sig[df_sig['label']=='{}'.format([0,1])]

1013 97.82496215860483


label  0  1  2  3  4  5  6  7  8  ...  bias 2455 bias 2456  bias 2457  \
0  [0, 1]  1  1  0  0  0  0  0  0  0  ...   0.071263  0.017044  -0.086233   

   bias 2458  bias 2459  bias 2460  bias 2461  bias 2462  bias 2463   Accuracy  
0  -0.416055   0.205376   0.138512   0.081432   0.150938  -0.189844  98.023333  

[1 rows x 2477 columns]

In [84]:
df_tan=pd.read_csv("./data/Weights tanh epoch 36.csv")

print(len(df_tan) ,df_tan['Accuracy'].mean() )
l=[0,1]
df_tan[df_tan['label']=='{}'.format([0,1])]

1013 98.6619661072721


label  0  1  2  3  4  5  6  7  8  ...  bias 2455 bias 2456  bias 2457  \
0  [0, 1]  1  1  0  0  0  0  0  0  0  ...  -0.050027   0.08467  -0.322452   

   bias 2458  bias 2459  bias 2460  bias 2461  bias 2462  bias 2463  Accuracy  
0  -0.071266   0.151368  -0.126146   0.435601   0.076297  -0.016888    98.245  

[1 rows x 2477 columns]

In [85]:
df_leak=pd.read_csv("./data/Weights leakyrelu epoch 36.csv")

print(len(df_leak) ,df_leak['Accuracy'].mean() )
l=[0,1]
df_leak[df_leak['label']=='{}'.format([0,1])]

1013 98.61952615992118


label  0  1  2  3  4  5  6  7  8  ...  bias 2455 bias 2456  bias 2457  \
0  [0, 1]  1  1  0  0  0  0  0  0  0  ...   0.429097 -0.088378  -0.135657   

   bias 2458  bias 2459  bias 2460  bias 2461  bias 2462  bias 2463   Accuracy  
0    -0.2474   0.325055   -0.08813   0.384046   -0.17395  -0.338969  98.831667  

[1 rows x 2477 columns]

In [31]:
listed=list(df_gel['label'].values)
alll=[f'{x}' for x in ListExperiences ]
missing_elements = set(alll) - set(listed)

print("Missing elements:", list(missing_elements))

NameError: name 'ListExperiences' is not defined

In [57]:
import ast

# Assuming s is the string created using f{}.format(L)
s = list(missing_elements)[0]

# Use ast.literal_eval to safely convert the string to a list
L = ast.literal_eval(s)
L_missing_elements=[ ast.literal_eval(list(missing_elements)[i]) for i in range(len(missing_elements)) ]
print(L_missing_elements)


NameError: name 'missing_elements' is not defined

In [86]:
df=pd.concat([df_gel, df_rel, df_sil,df_tan,df_sig,df_leak], ignore_index=True)
#df.tail().style.set_properties(subset=['Activation'], **{'width': '300px'})

In [87]:
from sklearn.preprocessing import LabelEncoder, OneHotEncoder
# Suppose 'string_feature' is the name of the string feature column in your DataFrame
string_feature = df['Activation']
# Label Encoding
label_encoder = LabelEncoder()
numeric_labels = label_encoder.fit_transform(list(df[df.columns[11]]))
numeric_labels

array([0, 0, 0, ..., 1, 1, 1])

In [88]:
onehot_encoder = OneHotEncoder(sparse=False)
onehot_encoded = onehot_encoder.fit_transform(numeric_labels.reshape(-1, 1))

# Replace the original string feature with the numeric or one-hot encoded features
df = pd.concat([df.drop('Activation', axis=1), pd.DataFrame(onehot_encoded)], axis=1)
df.head().style.set_properties(subset=list(df.columns[11:15]), **{'width': '300px'})

In [89]:
df=df.rename(columns={0: "gelu", 1: "relu", 2: "silu",3: "tanh", 4: "sigmoid", 5: "leakyrelu"}, errors="raise") 
df.head().style.set_properties(subset=list(df.columns[11:15]), **{'width': '300px'})

In [90]:
column_to_move = 'gelu'
desired_index = 11  # Set the desired index where you want to move the column

# Pop the column from its current position
column = df.pop(column_to_move)

# Insert the column at the desired index
df.insert(desired_index, column_to_move, column)


column_to_move = 'relu'
desired_index = 12  # Set the desired index where you want to move the column

# Pop the column from its current position
column = df.pop(column_to_move)

# Insert the column at the desired index
df.insert(desired_index, column_to_move, column)

column_to_move = 'silu'
desired_index = 13  # Set the desired index where you want to move the column

# Pop the column from its current position
column = df.pop(column_to_move)

# Insert the column at the desired index
df.insert(desired_index, column_to_move, column)
column_to_move = 'tanh'
desired_index = 14  # Set the desired index where you want to move the column

# Pop the column from its current position
column = df.pop(column_to_move)

# Insert the column at the desired index
df.insert(desired_index, column_to_move, column)
column_to_move = 'sigmoid'
desired_index = 15  # Set the desired index where you want to move the column

# Pop the column from its current position
column = df.pop(column_to_move)

# Insert the column at the desired index
df.insert(desired_index, column_to_move, column)
column_to_move = 'leakyrelu'
desired_index = 16  # Set the desired index where you want to move the column

# Pop the column from its current position
column = df.pop(column_to_move)

# Insert the column at the desired index
df.insert(desired_index, column_to_move, column)

df.head().style.set_properties(subset=list(df.columns[11:15]), **{'width': '300px'})

/tmp/ipykernel_89038/3818530914.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df.insert(desired_index, column_to_move, column)
/tmp/ipykernel_89038/3818530914.py:18: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df.insert(desired_index, column_to_move, column)
/tmp/ipykernel_89038/3818530914.py:27: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de

In [91]:
#df.tail().style.set_properties(subset=list(df.columns[11:15]), **{'width': '300px'})

In [9]:
Pairs_exp=list()
All=list(range(10))
for sample in range(2,9,1):
    S=combinations(range(10), sample)
    #All=list(range(10))
    for i in S :
        L1=list(i)
        L2=[k for k in All if k not in L1] 
        for sample2 in range(2,9,1):
            S2=combinations(L2, sample2)
            for j in S2:
                pair=[]
                pair.append(L1)
                sub=list(j)
                pair.append(sub)
                pair.sort()
                if pair not in Pairs_exp :
                    Pairs_exp.append(pair)
len(Pairs_exp)             

23436

In [10]:
train_pair=[]
train_tgt=[]

val_pair=[]
val_tgt=[]

test_pair=[]
test_tgt=[]
for pair in tqdm(Pairs_exp):
    if (len(pair[0])==5 and len(pair[1])==5) or(len(pair[0])==4 and len(pair[1])==4) or(len(pair[0])==3 and len(pair[1])==3) or (len(pair[0])==2 and len(pair[1])==2):
        test_pair.append(pair)
        tg=(pair[0]+pair[1]).sort()
        test_tgt.append(tg)
    elif (len(pair[0])==7 and len(pair[1])==2) or (len(pair[0])==2 and len(pair[1])==7) or (len(pair[0])==6 and len(pair[1])==3) or (len(pair[0])==3 and len(pair[1])==6) or (len(pair[0])==4 and len(pair[1])==5) or (len(pair[0])==5 and len(pair[1])==4):
        val_pair.append(pair)
        tg=(pair[0]+pair[1]).sort()
        val_tgt.append(tg)
    else :
        train_pair.append(pair)
        tg=(pair[0]+pair[1]).sort()
        train_tgt.append(tg)

100%|█████████████████████████████████| 23436/23436 [00:00<00:00, 904435.87it/s]


In [11]:
len(test_pair),len(train_pair),len(val_pair),len(test_tgt),len(train_tgt),len(val_tgt)

(4431, 16545, 2460, 4431, 16545, 2460)

In [12]:
df.to_csv("zoo epoch36.csv",index=False, header=True)

NameError: name 'df' is not defined

In [65]:
df[df['label']=='{}'.format([0,1])]['gelu']

0       1.0
1013    0.0
2026    0.0
3039    0.0
4052    0.0
5065    0.0
Name: gelu, dtype: float64

# Trainloader code

In [13]:
ListExperiences_=list()
All=list(range(10))
for sample in range(2,10,1):
    S=combinations(range(10), sample)
    #All=list(range(10))
    for i in S :
        L1=list(i)
        L2=[k for k in All if k not in L1] 
        ListExperiences_.append(L1)
len(ListExperiences_)
ListExperiences_.append([x for x in range(10)])

In [14]:
df=pd.read_csv("zoo epoch11.csv")
params_cols=list(df.columns[17:-1])
params_cols[:10]

['weight 0',
 'weight 1',
 'weight 2',
 'weight 3',
 'weight 4',
 'weight 5',
 'weight 6',
 'weight 7',
 'weight 8',
 'weight 9']

In [15]:
df.head()

label  0  1  2  3  4  5  6  7  8  ...  bias 2455  bias 2456  bias 2457  \
0  [0, 1]  1  1  0  0  0  0  0  0  0  ...   0.247331  -0.101165  -0.123394   
1  [0, 2]  1  0  1  0  0  0  0  0  0  ...  -0.007754  -0.062117   0.038516   
2  [0, 3]  1  0  0  1  0  0  0  0  0  ...   0.531460  -0.036903  -0.451388   
3  [0, 4]  1  0  0  0  1  0  0  0  0  ...   0.100621   0.100433   0.221786   
4  [0, 5]  1  0  0  0  0  1  0  0  0  ...   0.204960  -0.109625  -0.115857   

   bias 2458  bias 2459  bias 2460  bias 2461  bias 2462  bias 2463   Accuracy  
0  -0.139609   0.238313  -0.040772   0.191127  -0.071601  -0.135258  98.091667  
1   0.119955   0.415654  -0.163165  -0.104250   0.108712  -0.193884  97.706667  
2  -0.119526  -0.141796  -0.079200   0.474600   0.041734  -0.180028  97.571667  
3  -0.120229   0.152037  -0.075444  -0.050731  -0.016240  -0.102277  98.086667  
4   0.117505  -0.021782  -0.138023   0.019041   0.004474   0.084009  97.778333  

[5 rows x 2482 columns]

In [16]:
Pairs_exp=list()
All=list(range(10))
for sample in range(2,9,1):
    S=combinations(range(10), sample)
    #All=list(range(10))
    for i in S :
        L1=list(i)
        L2=[k for k in All if k not in L1] 
        for sample2 in range(2,9,1):
            S2=combinations(L2, sample2)
            for j in S2:
                pair=[]
                pair.append(L1)
                sub=list(j)
                pair.append(sub)
                pair.sort()
                if pair not in Pairs_exp :
                    Pairs_exp.append(pair)
print(len(Pairs_exp))
train_pair=[]
train_tgt=[]

val_pair=[]
val_tgt=[]

test_pair=[]
test_tgt=[]

for pair in tqdm(Pairs_exp):
    if (len(pair[0])==5 and len(pair[1])==5) or(len(pair[0])==4 and len(pair[1])==4) or(len(pair[0])==3 and len(pair[1])==3) or (len(pair[0])==2 and len(pair[1])==2):
        test_pair.append(pair)
        tg=(pair[0]+pair[1]).sort()
        test_tgt.append(tg)
    elif (len(pair[0])==7 and len(pair[1])==2) or (len(pair[0])==2 and len(pair[1])==7) or (len(pair[0])==6 and len(pair[1])==3) or (len(pair[0])==3 and len(pair[1])==6) or (len(pair[0])==4 and len(pair[1])==5) or (len(pair[0])==5 and len(pair[1])==4):
        val_pair.append(pair)
        tg=(pair[0]+pair[1]).sort()
        val_tgt.append(tg)
    else :
        train_pair.append(pair)
        tg=(pair[0]+pair[1]).sort()
        train_tgt.append(tg)

23436


100%|████████████████████████████████| 23436/23436 [00:00<00:00, 1014434.71it/s]


In [17]:
from torch.utils.data import TensorDataset

In [18]:
'''
L_Stream1=[]
L_Stream2=[]
tgt=[]
L_activations=["gelu","relu","silu","leakyrelu","sigmoid","tanh"]
for activ in L_activations: 
    L_Stream1=[]
    L_Stream2=[]
    tgt=[]
    for c,pair in tqdm(enumerate(val_pair)): #test , val
        L_Stream1.append(torch.from_numpy(df[(df['label']=='{}'.format(pair[0])) & (df[activ]==float(1)) ][params_cols].to_numpy().astype('float64')))
        L_Stream2.append(torch.from_numpy(df[(df['label']=='{}'.format(pair[0])) & (df[activ]==float(1)) ][params_cols].to_numpy().astype('float64')))
        tg=pair[0]+pair[1]
        tg.sort()
        #print(tg)
        tgt.append(torch.from_numpy(df[ (df['label']=='{}'.format(tg)) & (df[activ]==float(1) )][params_cols].to_numpy().astype('float64')))
        if c%30==0 and (c//30)>0:
            Stream1=torch.stack(L_Stream1)
            Stream2=torch.stack(L_Stream2)
            target=torch.stack(tgt)
            Stream1=torch.reshape(Stream1, (Stream1.shape[0], Stream1.shape[2]))
            Stream2=torch.reshape(Stream2, (Stream2.shape[0], Stream2.shape[2]))
            target=torch.reshape(target, (target.shape[0], target.shape[2]))
            train_dataset = TensorDataset(Stream1,Stream2, target)
            torch.save(train_dataset, f'.//data//Training Batches//val//val_dataset_{activ}_Batch_{c//30}.pt')
            L_Stream1=[]
            L_Stream2=[]
            tgt=[]
'''            

'\nL_Stream1=[]\nL_Stream2=[]\ntgt=[]\nL_activations=["gelu","relu","silu","leakyrelu","sigmoid","tanh"]\nfor activ in L_activations: \n    L_Stream1=[]\n    L_Stream2=[]\n    tgt=[]\n    for c,pair in tqdm(enumerate(val_pair)): #test , val\n        L_Stream1.append(torch.from_numpy(df[(df[\'label\']==\'{}\'.format(pair[0])) & (df[activ]==float(1)) ][params_cols].to_numpy().astype(\'float64\')))\n        L_Stream2.append(torch.from_numpy(df[(df[\'label\']==\'{}\'.format(pair[0])) & (df[activ]==float(1)) ][params_cols].to_numpy().astype(\'float64\')))\n        tg=pair[0]+pair[1]\n        tg.sort()\n        #print(tg)\n        tgt.append(torch.from_numpy(df[ (df[\'label\']==\'{}\'.format(tg)) & (df[activ]==float(1) )][params_cols].to_numpy().astype(\'float64\')))\n        if c%30==0 and (c//30)>0:\n            Stream1=torch.stack(L_Stream1)\n            Stream2=torch.stack(L_Stream2)\n            target=torch.stack(tgt)\n            Stream1=torch.reshape(Stream1, (Stream1.shape[0], Strea

In [ ]:
'''
from torch.utils.data import TensorDataset, ConcatDataset, DataLoader
L_Datasets=[]
L_activations=["gelu","relu","silu","leakyrelu","sigmoid","tanh"]
for activ in L_activations: 
    dsa=torch.load(f'train_dataset_{activ}.pt')
    L_Datasets.append(dsa)
dsab_cat = ConcatDataset(L_Datasets)
dsab_cat_loader = DataLoader(dsab_cat)
'''

In [14]:
#len(dsab_cat_loader)

99270

In [19]:
from torch.utils.data import TensorDataset, ConcatDataset, DataLoader
class CustomDataset(TensorDataset): #L_activations=["gelu","relu","silu","leakyrelu","sigmoid","tanh"]
    def __init__(self,L_exp,start_idx,end_idex,df_path="zoo epoch11.csv",activ="gelu"):
        self.activ=activ
        L_Stream1=[]
        L_Stream2=[]
        tgt=[]
        self.df_path = df_path
        self.start_idx=start_idx
        self.end_idx=end_idex
        self.df=pd.read_csv(df_path)
        self.L_exp=L_exp
        params_cols=list(df.columns[17:-1])
        params_cols[:10]
        #self.transform = transforms.ToTensor()
        for c,pair in tqdm(enumerate(self.L_exp[self.start_idx:self.end_idx])): #test , val
            L_Stream1.append(torch.from_numpy(self.df[(self.df['label']=='{}'.format(pair[0])) & (self.df[self.activ]==float(1)) ][params_cols].to_numpy().astype('float64')))
            L_Stream2.append(torch.from_numpy(self.df[(self.df['label']=='{}'.format(pair[1])) & (self.df[self.activ]==float(1)) ][params_cols].to_numpy().astype('float64')))
            tg=pair[0]+pair[1]
            tg.sort()
            #print(tg)
            tgt.append(torch.from_numpy(self.df[ (self.df['label']=='{}'.format(tg)) & (self.df[self.activ]==float(1) )][params_cols].to_numpy().astype('float64')))
        Stream1=torch.stack(L_Stream1)
        Stream2=torch.stack(L_Stream2)
        target=torch.stack(tgt)
        Stream1=torch.reshape(Stream1, (Stream1.shape[0], Stream1.shape[2]))
        Stream2=torch.reshape(Stream2, (Stream2.shape[0], Stream2.shape[2]))
        target=torch.reshape(target, (target.shape[0], target.shape[2]))
        train_dataset = TensorDataset(Stream1,Stream2, target)
        self.loaded=train_dataset
        self.loaded_exp=self.L_exp[self.start_idx:self.end_idx]
    def __len__(self):
        return len(self.L_exp[self.start_idx:self.end_idx])

    def __getitem__(self, idx):
        q=0
        for x1,x2,tg in self.loaded:
            #print(self.L_exp[:20],x1.shape,x2.shape,tg.shape)
            if q==idx :
                #print(self.loaded_exp[idx])
                return x1,x2,tg,self.loaded_exp[idx]
            elif idx>=self.end_idx-self.start_idx:
                break
            else:
                q=q+1

In [20]:
cs=CustomDataset(val_pair,0,30)

30it [00:00, 277.18it/s]


In [21]:
cs[0]
cs.loaded_exp
cs=CustomDataset(val_pair,0,30)
for x1,x2,tg,labels in DataLoader(cs):
    print(x1.shape)
    print([x.item() for x in labels[0]])
    break

30it [00:00, 289.67it/s]

torch.Size([1, 2464])
[0, 1]


# Autoencoder

In [22]:
class PositionalEncoder(nn.Module):
    def __init__(self, d_model, max_seq_len=80, device="cpu"):
        super().__init__()
        self.d_model = d_model
        self.device = device

        # create constant 'pe' matrix with values dependant on
        # pos and i
        self.pe = self._generate_positional_encoding(max_seq_len, d_model)

    def forward(self, x):
        # make embeddings relatively larger
        x = x * math.sqrt(self.d_model)
        # add constant to embedding
        seq_len = x.size(1)
        # dynamically adjust positional encoding matrix based on sequence length
        pe = self.pe[:, :seq_len]
        x = x + pe
        return x

    def _generate_positional_encoding(self, max_seq_len, d_model):
        pe = torch.zeros(max_seq_len, d_model)
        position = torch.arange(0, max_seq_len, dtype=torch.float).unsqueeze(1)
        div_term = torch.exp(torch.arange(0, d_model, 2).float() * (-math.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)
        pe[:, 1::2] = torch.cos(position * div_term)
        pe = pe.unsqueeze(0)
        return pe

In [23]:
class EncoderNeuronGroup(nn.Module):
    def __init__(self, d_model, N, heads, max_seq_len, dropout, d_ff):
        super().__init__()
        self.N = N
        self.embed = EmbedderNeuronGroup(d_model)
        self.pe = PositionalEncoder(d_model, max_seq_len)
        print("decoder droupout init",dropout)
        self.layers = get_clones(EncoderLayer(d_model, heads, normalize=True,dropout=dropout, d_ff=d_ff), N)
        self.norm = Norm(d_model)

    def forward(self, src, mask=None):
        scores = []
        x = self.embed(src)
        x = self.pe(x)
        for i in range(self.N):
            x, sc = self.layers[i](x, mask)
            scores.append(sc)
        #print("scores variable shape is:",scores[0][0].shape," norm variable shape is:",self.norm(x).shape)
        #print(scores[0][0])
        return self.norm(x), scores

class DecoderNeuronGroup(nn.Module):
    def __init__(self, d_model, N, heads, max_seq_len, dropout, d_ff, neck):
        super().__init__()
        self.N = N
        self.embed = Neck2Seq(d_model, neck,max_seq_len)
        self.pe = PositionalEncoder(d_model, max_seq_len)
        print("decoder droupout init",dropout)
        self.layers = get_clones(EncoderLayer(d_model, heads,normalize=True,dropout=dropout, d_ff=d_ff), N)
        self.norm = Norm(d_model)

        self.lay = Seq2Vec(d_model=d_model,max_seq_len=max_seq_len)

    def forward(self, src, mask=None):
        scores = []
        x = self.embed(src)
        x = self.pe(x)
        for i in range(self.N):
            x, sc = self.layers[i](x, mask)
            scores.append(sc)
        return self.lay(self.norm(x)), scores

In [24]:
class EmbedderNeuronGroup(nn.Module):
    def __init__(self, d_model, seed=22):
        super().__init__()
        print("EmbedderNeuroneGroup")
        self.neuron_l1 = nn.Linear(16, d_model)
        self.neuron_l2 = nn.Linear(5, d_model)

    def forward(self, x):
        return self.multiLinear(x)

    def multiLinear(self, v):
        #print(v.shape)
        # Hardcoded position for easy-fast integration
        l = []
        # l1
        if v.shape[1]==100:
            for ndx in range(5):
                idx_start = ndx * 16
                idx_end = idx_start + 16
                l.append(self.neuron_l1(v[:, idx_start:idx_end]))
                
            # l2
            for ndx in range(4):
                idx_start = 5 * 16 + ndx * 5
                idx_end = idx_start + 5
                l.append(self.neuron_l2(v[:, idx_start:idx_end]))

        if v.shape[1]==2464:
            for g in range(25):
                if g==24:
                    for ndx in range(4):
                        idx_start = g*100 + ndx * 16
                        idx_end = idx_start + 16
                        l.append(self.neuron_l1(v[:, idx_start:idx_end]))
                        #print(v[:, idx_start:idx_end].shape)
                else:     
                    for ndx in range(5):
                        idx_start =g*100 + ndx * 16
                        idx_end = idx_start + 16
                        l.append(self.neuron_l1(v[:, idx_start:idx_end]))
                        #print(v[:, idx_start:idx_end].shape)
                    # l2
                    for ndx in range(4):
                        idx_start = g*100 + 5 * 16 + ndx * 5
                        idx_end = idx_start + 5
                        l.append(self.neuron_l2(v[:, idx_start:idx_end]))
                        #print(v[:, idx_start:idx_end].shape)
        #print(len(l))
        #print(len(l[0]))
        final = torch.stack(l, dim=1)

        # print(final.shape)
        return final

class DebedderNeuronGroup(nn.Module):
    def __init__(self, d_model, max_seq_len):
        super().__init__()
        self.d_model = d_model
        self.max_seq_len = max_seq_len
        self.linear1 = nn.Linear(d_model, 16)
        self.linear2 = nn.Linear(d_model, 5)

    def forward(self, x):
        return self.multiLinear(x)

    def multiLinear(self, x):
        segments = []
        for i in range(x.size(1)):
            if i < self.max_seq_len // 2:
                segment = self.linear1(x[:, i])
            else:
                segment = self.linear2(x[:, i])
            segments.append(segment)

        reconstructed = torch.cat(segments, dim=1)
        return reconstructed

In [25]:
import torch
import torch.nn as nn
import numpy as np


from torch.utils.tensorboard import SummaryWriter
import itertools
from einops import repeat

from einops import repeat

import torch.nn as nn
import torch.nn.functional as F
import math, copy, time
from torch.autograd import Variable


# # Transformer Shared Layers


def get_clones(module, N):
    return nn.ModuleList([copy.deepcopy(module) for i in range(N)])
class PositionalEncoder(nn.Module):
    def __init__(self, d_model, max_seq_len=80, device="cpu"):
        super().__init__()
        self.d_model = d_model
        self.device = device

        # create constant 'pe' matrix with values dependant on
        # pos and i
        self.pe = self._generate_positional_encoding(max_seq_len, d_model)

    def forward(self, x):
        # make embeddings relatively larger
        x = x * math.sqrt(self.d_model)
        # add constant to embedding
        seq_len = x.size(1)
        # dynamically adjust positional encoding matrix based on sequence length
        pe = self.pe[:, :seq_len]
        x = x + pe
        return x

    def _generate_positional_encoding(self, max_seq_len, d_model):
        pe = torch.zeros(max_seq_len, d_model)
        position = torch.arange(0, max_seq_len, dtype=torch.float).unsqueeze(1)
        div_term = torch.exp(torch.arange(0, d_model, 2).float() * (-math.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)
        pe[:, 1::2] = torch.cos(position * div_term)
        pe = pe.unsqueeze(0)
        return pe

In [26]:
class Neck2Seq(nn.Module):
    def __init__(self, d_model, neck,max_seq_length):
        super().__init__()
        self.neurons = nn.ModuleList([nn.Linear(neck, d_model) for _ in range(max_seq_length)])
    def forward(self, x):
        l = [neuron(x) for neuron in self.neurons]
        final = torch.stack(l, dim=1)
        return final
'''    
class Seq2Vec(nn.Module):
    def __init__(self, d_model, max_seq_len):
        super().__init__()
        self.num_neurons = 20  # Number of linear transformations
        self.d_model = d_model
        self.max_seq_len = max_seq_len

        # Define linear layers
        self.neurons = nn.ModuleList([
            nn.Linear(d_model, 16) if i < 5 else nn.Linear(d_model, 5)
            for i in range(self.num_neurons)
        ])

    def forward(self, x):
        return self.multiLinear(x)
    
    def multiLinear(self, v):
        l = []
        print(self.neurons)
        print("shape of v",v.shape)
        for i in range(self.max_seq_len):
            #print(i)
            # Apply the appropriate linear transformation
            #print("i% num neurons",self.neurons[i % self.num_neurons])
            #print("i% num neurons tensor access",self.neurons[i % self.num_neurons](v[:, i]))
            neuron_output = self.neurons[i % self.num_neurons](v[:, i])
            #print(neuron_output.shape)
            l.append(neuron_output)
        
        final = torch.cat(l, dim=1)  # Concatenate tensors along the feature dimension (dim=1)
        return final
'''
class Seq2Vec(nn.Module):
    def __init__(self, d_model, max_seq_len):
        super().__init__()
        self.num_neurons = 20  # Number of linear transformations
        self.d_model = d_model
        self.max_seq_len = max_seq_len

        # Define linear layers
        self.neurons = nn.ModuleList([
            nn.Linear(max_seq_len, d_model) if i < 5 else nn.Linear(max_seq_len, d_model)
            for i in range(self.num_neurons)
        ])

    def forward(self, x):
        return self.multiLinear(x)

    def multiLinear(self, v):
        l = []
        for i in range(self.max_seq_len):
            # Reshape the input tensor to (batch_size, neck)
            x = v[:, :, i].squeeze(1)
            # Apply the appropriate linear transformation
            neuron_output = self.neurons[i % self.num_neurons](x)
            l.append(neuron_output)
        
        final = torch.cat(l, dim=1)  # Concatenate tensors along the feature dimension (dim=1)
        return final


In [27]:
class FeedForward(nn.Module):
    def __init__(self, d_model, d_ff=2048, dropout=0.1):
        super().__init__()
        # We set d_ff as a default to 2048
        self.linear_1 = nn.Linear(d_model, d_ff)
        self.dropout = nn.Dropout(dropout)
        self.linear_2 = nn.Linear(d_ff, d_model)

    def forward(self, x):
        x = self.dropout(F.relu(self.linear_1(x)))
        x = self.linear_2(x)
        return x


class Norm(nn.Module):
    def __init__(self, d_model, eps=1e-6):
        super().__init__()

        self.size = d_model
        # create two learnable parameters to calibrate normalisation
        self.alpha = nn.Parameter(torch.ones(self.size))
        self.bias = nn.Parameter(torch.zeros(self.size))
        self.eps = eps

    def forward(self, x):
        norm = (
            self.alpha
            * (x - x.mean(dim=-1, keepdim=True))
            / (x.std(dim=-1, keepdim=True) + self.eps)
            + self.bias
        )
        return norm

In [28]:
def attention(q, k, v, d_k, mask=None, dropout=None):
    scores = torch.matmul(q, k.transpose(-2, -1)) / math.sqrt(d_k)
    if mask is not None:
        mask = mask.unsqueeze(1)
        scores = scores.masked_fill(mask == 0, -1e9)
    scores = F.softmax(scores, dim=-1)

    if dropout is not None:
        scores = dropout(scores)

    output = torch.matmul(scores, v)

    return output, scores





class MultiHeadAttention(nn.Module):
    def __init__(self, heads, d_model, dropout=0.1):
        super().__init__()
        
        self.d_model = d_model
        self.d_k = d_model // heads
        self.h = heads

        self.q_linear = nn.Linear(d_model, d_model)
        self.v_linear = nn.Linear(d_model, d_model)
        self.k_linear = nn.Linear(d_model, d_model)
        self.dropout = nn.Dropout(dropout)
        self.out = nn.Linear(d_model, d_model)

    def forward(self, q, k, v, mask=None):

        bs = q.size(0)

        # perform linear operation and split into h heads

        k = self.k_linear(k).view(bs, -1, self.h, self.d_k)
        q = self.q_linear(q).view(bs, -1, self.h, self.d_k)
        v = self.v_linear(v).view(bs, -1, self.h, self.d_k)

        # transpose to get dimensions bs * h * sl * d_model

        k = k.transpose(1, 2)
        q = q.transpose(1, 2)
        v = v.transpose(1, 2)
        # calculate attention using function we will define next
        scores, sc = attention(q, k, v, self.d_k, mask, self.dropout)

        # concatenate heads and put through final linear layer
        concat = scores.transpose(1, 2).contiguous().view(bs, -1, self.d_model)

        output = self.out(concat)

        return output, sc


class EncoderLayer(nn.Module):
    def __init__(self, d_model, heads, normalize=True, dropout=0.1, d_ff=2048):
        super().__init__()
        self.normalize = normalize
        if normalize:
            self.norm_1 = Norm(d_model)
            self.norm_2 = Norm(d_model)
        self.attn = MultiHeadAttention(heads, d_model, dropout=dropout)
        self.ff = FeedForward(d_model, d_ff=d_ff, dropout=dropout)
        self.dropout_1 = nn.Dropout(dropout)
        self.dropout_2 = nn.Dropout(dropout)

    def forward(self, x, mask):
        if self.normalize:
            x2 = self.norm_1(x)
        else:
            x2 = x.clone()
        res, sc = self.attn(x2, x2, x2, mask)
        # x = x + self.dropout_1(self.attn(x2,x2,x2,mask))
        x = x + self.dropout_1(res)
        if self.normalize:
            x2 = self.norm_2(x)
        else:
            x2 = x.clone()
        x = x + self.dropout_2(self.ff(x2))
        # return x
        return x, sc


class Encoder(nn.Module):
    def __init__(
        self, input_dim, d_model, N, heads, max_seq_len, dropout, d_ff, device
    ):
        super().__init__()
        self.device = device
        self.N = N
        self.embed = Embedder(input_dim, d_model)
        self.pe = PositionalEncoder(d_model, max_seq_len, device)
        self.layers = get_clones(EncoderLayer(d_model, heads, dropout, d_ff), N)
        self.norm = Norm(d_model)

    def forward(self, src, mask=None):
        scores = []
        x = self.embed(src)
        x = self.pe(x)
        for i in range(self.N):
            x, sc = self.layers[i](x, mask)
            scores.append(sc)
        return self.norm(x), scores

In [29]:
class TransformerAE(nn.Module):
    def __init__(
        self,
        max_seq_len=9,
        N=1,
        heads=1,
        d_model=100,
        d_ff=100,
        neck=20,
        dropout=0.1,
        **kwargs,):
        super().__init__()
        self.N=N
        self.heads=heads
        self.dropout=dropout
        self.d_ff=d_ff
        self.d_model=d_model
        self.max_seq_len=max_seq_len
        self.neck=neck

            
        self.enc1 = EncoderNeuronGroup(d_model=self.d_model, N=self.N, heads=self.heads, max_seq_len=self.max_seq_len, dropout=self.dropout,d_ff=self.d_ff)
        self.enc2 = EncoderNeuronGroup(d_model=self.d_model, N=self.N, heads=self.heads, max_seq_len=self.max_seq_len, dropout=self.dropout,d_ff=self.d_ff)
        self.dec = DecoderNeuronGroup(d_model=self.d_model, N=self.N, heads=self.heads, max_seq_len=self.max_seq_len, dropout=self.dropout,d_ff=self.d_ff,neck=self.neck)
        # Addition Approach
        #print("Addition Approach!")
        self.vec2neck = nn.Linear(self.d_ff, self.max_seq_len)
        # Stacking Approach
        #print("Stack Approach!")
        #self.vec2neck = nn.Linear(2*self.d_ff * self.max_seq_len, self.neck)

        self.tanh = nn.Tanh()

        # Xavier Uniform Initialitzation
        for p in self.parameters():
            if p.dim() > 1:
                nn.init.xavier_uniform_(p)

    def forward(self, inp1,inp2):

        # First Approach
        out1, scEnc1 = self.enc1(inp1)
        #print(out1.shape)
        out2, scEnc2 = self.enc2(inp2)
        out3=torch.cat([out1,out2], dim=2)
        #print("out3",out3.shape,"d_ff *2",self.d_ff*2)
        #print("dim 0",torch.sum(out3, dim=0, keepdim=False).shape)
        #print("dim 1",torch.sum(out3, dim=1, keepdim=False).shape)
        #print("dim 2",torch.sum(out3, dim=2, keepdim=False).shape)
        #print("neck",self.neck)
        # Addition
        neck = self.tanh(self.vec2neck(torch.sum(out3, dim=1, keepdim=False)))

        # Stacking
        #out3 = out3.view(out3.shape[0], out3.shape[1] * out3.shape[2])
        #neck = self.tanh(self.vec2neck(out3))

        out, scDec = self.dec(neck)

        return out, neck, scEnc1,scEnc2, scDec

    def count_parameters(self, model):
        return sum(p.numel() for p in model.parameters() if p.requires_grad)

    def numParams(self):
        encNumParams = self.count_parameters(self.enc1)
        neckNumParams = self.count_parameters(self.vec2neck)
        decNumParams = self.count_parameters(self.dec)
        modelParams = self.count_parameters(self)

        return (
            "EncParams: {}, NeckParams: {}, DecParams: {}, || ModelParams: {} ".format(
                encNumParams, neckNumParams, decNumParams, modelParams
            )
        )

In [36]:
del(mod)

In [29]:
mod = TransformerAE(max_seq_len=9, 
                    N=1, 
                    heads=5, 
                    d_model=100, 
                    d_ff=200,
                    neck=20 ,
                    dropout=0.1
                   )

EmbedderNeuroneGroup
decoder droupout init 0.1
EmbedderNeuroneGroup
decoder droupout init 0.1
decoder droupout init 0.1


In [30]:
len(test_pair),len(train_pair),len(val_pair),len(test_tgt),len(train_tgt),len(val_tgt)

(4431, 16545, 2460, 4431, 16545, 2460)

In [31]:
#AAA
'''
mod = TransformerAE(max_seq_len=9, 
                    N=1, 
                    heads=5, 
                    d_model=100, 
                    d_ff=200,
                    neck=20 ,
                    dropout=0.1
                   )
'''

print(mod.numParams())
#device = torch.device('cuda:0')

vec1 = torch.rand(10,100)
vec2 = torch.rand(10,100)

#vec1 = torch.rand(10,100)
#vec2 = torch.rand(10,100)
vec3 = torch.rand(10,100)
#print("------------",vec1.shape , x1[0,:].shape)
#mod=mod.to(device)
#vec1=vec1.to(device)
#vec2=vec2.to(device)

#x1=x1.to(torch.float32)
#x2=x2.to(torch.float32)
#x1=x1.to(device)
#x2=x2.to(device)
#print("------------",vec1.shape , x1[0,:].shape)
out = mod(vec1,vec2)
print("Output Shape: ", out[0].shape)
# Training Params
#batchSize = 1000
#criterion = torch.nn.MSELoss(reduction='mean')
#optimizer = torch.optim.Adam(mod.parameters(), lr=1e-3, weight_decay=1e-9)
from torchinfo import summary

summary(mod )#[(10,100), (10,100)]



EncParams: 83600, NeckParams: 4020, DecParams: 115855, || ModelParams: 287075 
ModuleList(
  (0): Linear(in_features=100, out_features=16, bias=True)
  (1): Linear(in_features=100, out_features=16, bias=True)
  (2): Linear(in_features=100, out_features=16, bias=True)
  (3): Linear(in_features=100, out_features=16, bias=True)
  (4): Linear(in_features=100, out_features=16, bias=True)
  (5): Linear(in_features=100, out_features=5, bias=True)
  (6): Linear(in_features=100, out_features=5, bias=True)
  (7): Linear(in_features=100, out_features=5, bias=True)
  (8): Linear(in_features=100, out_features=5, bias=True)
  (9): Linear(in_features=100, out_features=5, bias=True)
  (10): Linear(in_features=100, out_features=5, bias=True)
  (11): Linear(in_features=100, out_features=5, bias=True)
  (12): Linear(in_features=100, out_features=5, bias=True)
  (13): Linear(in_features=100, out_features=5, bias=True)
  (14): Linear(in_features=100, out_features=5, bias=True)
  (15): Linear(in_features=10

Layer (type:depth-idx)                        Param #
TransformerAE                                 --
├─EncoderNeuronGroup: 1-1                     --
│    └─EmbedderNeuronGroup: 2-1               --
│    │    └─Linear: 3-1                       1,700
│    │    └─Linear: 3-2                       600
│    └─PositionalEncoder: 2-2                 --
│    └─ModuleList: 2-3                        --
│    │    └─EncoderLayer: 3-3                 81,100
│    └─Norm: 2-4                              200
├─EncoderNeuronGroup: 1-2                     --
│    └─EmbedderNeuronGroup: 2-5               --
│    │    └─Linear: 3-4                       1,700
│    │    └─Linear: 3-5                       600
│    └─PositionalEncoder: 2-6                 --
│    └─ModuleList: 2-7                        --
│    │    └─EncoderLayer: 3-6                 81,100
│    └─Norm: 2-8                              200
├─DecoderNeuronGroup: 1-3                     --
│    └─Neck2Seq: 2-9                          

In [29]:
criterion = nn.L1Loss()
optimizer = Adam(mod.parameters(), lr=0.0005)
scheduler = torch.optim.lr_scheduler.CyclicLR(optimizer, base_lr=1e-5, max_lr=0.0005, step_size_up=200, mode="triangular2", cycle_momentum=False)
num_epochs=40
L=[]
for epoch in tqdm(range(num_epochs)):
    mod.train()
    optimizer.zero_grad()
    output = mod(vec1,vec2)

    #print(labels[0],x1.shape,tg.shape,output[0].shape)
    loss = criterion(output[0],vec3)
    loss.backward()
    optimizer.step()
    L.append(loss.item())
    scheduler.step()

 18%|███████▋                                    | 7/40 [00:00<00:00, 65.94it/s]

ModuleList(
  (0): Linear(in_features=100, out_features=16, bias=True)
  (1): Linear(in_features=100, out_features=16, bias=True)
  (2): Linear(in_features=100, out_features=16, bias=True)
  (3): Linear(in_features=100, out_features=16, bias=True)
  (4): Linear(in_features=100, out_features=16, bias=True)
  (5): Linear(in_features=100, out_features=5, bias=True)
  (6): Linear(in_features=100, out_features=5, bias=True)
  (7): Linear(in_features=100, out_features=5, bias=True)
  (8): Linear(in_features=100, out_features=5, bias=True)
  (9): Linear(in_features=100, out_features=5, bias=True)
  (10): Linear(in_features=100, out_features=5, bias=True)
  (11): Linear(in_features=100, out_features=5, bias=True)
  (12): Linear(in_features=100, out_features=5, bias=True)
  (13): Linear(in_features=100, out_features=5, bias=True)
  (14): Linear(in_features=100, out_features=5, bias=True)
  (15): Linear(in_features=100, out_features=5, bias=True)
  (16): Linear(in_features=100, out_features=5, b

 65%|███████████████████████████▉               | 26/40 [00:00<00:00, 82.99it/s]

ModuleList(
  (0): Linear(in_features=100, out_features=16, bias=True)
  (1): Linear(in_features=100, out_features=16, bias=True)
  (2): Linear(in_features=100, out_features=16, bias=True)
  (3): Linear(in_features=100, out_features=16, bias=True)
  (4): Linear(in_features=100, out_features=16, bias=True)
  (5): Linear(in_features=100, out_features=5, bias=True)
  (6): Linear(in_features=100, out_features=5, bias=True)
  (7): Linear(in_features=100, out_features=5, bias=True)
  (8): Linear(in_features=100, out_features=5, bias=True)
  (9): Linear(in_features=100, out_features=5, bias=True)
  (10): Linear(in_features=100, out_features=5, bias=True)
  (11): Linear(in_features=100, out_features=5, bias=True)
  (12): Linear(in_features=100, out_features=5, bias=True)
  (13): Linear(in_features=100, out_features=5, bias=True)
  (14): Linear(in_features=100, out_features=5, bias=True)
  (15): Linear(in_features=100, out_features=5, bias=True)
  (16): Linear(in_features=100, out_features=5, b

100%|███████████████████████████████████████████| 40/40 [00:00<00:00, 84.80it/s]

ModuleList(
  (0): Linear(in_features=100, out_features=16, bias=True)
  (1): Linear(in_features=100, out_features=16, bias=True)
  (2): Linear(in_features=100, out_features=16, bias=True)
  (3): Linear(in_features=100, out_features=16, bias=True)
  (4): Linear(in_features=100, out_features=16, bias=True)
  (5): Linear(in_features=100, out_features=5, bias=True)
  (6): Linear(in_features=100, out_features=5, bias=True)
  (7): Linear(in_features=100, out_features=5, bias=True)
  (8): Linear(in_features=100, out_features=5, bias=True)
  (9): Linear(in_features=100, out_features=5, bias=True)
  (10): Linear(in_features=100, out_features=5, bias=True)
  (11): Linear(in_features=100, out_features=5, bias=True)
  (12): Linear(in_features=100, out_features=5, bias=True)
  (13): Linear(in_features=100, out_features=5, bias=True)
  (14): Linear(in_features=100, out_features=5, bias=True)
  (15): Linear(in_features=100, out_features=5, bias=True)
  (16): Linear(in_features=100, out_features=5, b

In [30]:
#AAA
mod = TransformerAE(max_seq_len=2464, 
                    N=5, 
                    heads=1, 
                    d_model=2464, 
                    d_ff=4928,
                    neck=30,
                    dropout=0.1
                   )

print(mod.numParams())

#mod=mod.to(device)

x1=x1.to(torch.float32)
x2=x2.to(torch.float32)
#x1=x1.to(device)
#x2=x2.to(device)

out = mod(x1,x2)
print("Output Shape: ", out[0].shape)
# Training Params
#batchSize = 1000
#criterion = torch.nn.MSELoss(reduction='mean')
#optimizer = torch.optim.Adam(mod.parameters(), lr=1e-3, weight_decay=1e-9)
from torchinfo import summary

summary(mod)


EmbedderNeuroneGroup
decoder droupout init 0.1
EmbedderNeuroneGroup
decoder droupout init 0.1
decoder droupout init 0.1
EncParams: 243048960, NeckParams: 12145056, DecParams: 552677664, || ModelParams: 1050920640 


RuntimeError: mat1 and mat2 shapes cannot be multiplied (1x2464 and 30x2464)

In [26]:
criterion = nn.L1Loss()
optimizer = Adam(mod.parameters(), lr=0.0005)
scheduler = torch.optim.lr_scheduler.CyclicLR(optimizer, base_lr=1e-5, max_lr=0.0005, step_size_up=200, mode="triangular2", cycle_momentum=False)
num_epochs=40
L=[]
for epoch in tqdm(range(num_epochs)):
    for mul in range(len(train_pair)//30):
        cs=CustomDataset(train_pair,mul*30,min((mul+1)*30,len(train_pair)))
        for x1,x2,tg,labels in DataLoader(cs):
            x1=x1.to(torch.float32)
            x2=x2.to(torch.float32)
            #x1=x1.to(device)
            #x2=x2.to(device)
            
            mod.train()
            #mod=mod.to(device)
            optimizer.zero_grad()
            output = mod(x1,x2)
            
            print(labels[0],x1.shape,tg.shape,output[0].shape)
            loss = criterion(output[0],tg)
            loss.backward()
            optimizer.step()
            L.append(loss.item())
            scheduler.step()

  0%|                                                    | 0/40 [00:00<?, ?it/s]
0it [00:00, ?it/s]
30it [00:00, 277.19it/s]
/home/crns/anaconda3/lib/python3.9/site-packages/torch/nn/modules/loss.py:96: UserWarning: Using a target size (torch.Size([1, 2464])) that is different to the input size (torch.Size([1, 19129])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.l1_loss(input, target, reduction=self.reduction)
  0%|                                                    | 0/40 [00:04<?, ?it/s]

ModuleList(
  (0): Linear(in_features=2464, out_features=16, bias=True)
  (1): Linear(in_features=2464, out_features=16, bias=True)
  (2): Linear(in_features=2464, out_features=16, bias=True)
  (3): Linear(in_features=2464, out_features=16, bias=True)
  (4): Linear(in_features=2464, out_features=16, bias=True)
  (5): Linear(in_features=2464, out_features=5, bias=True)
  (6): Linear(in_features=2464, out_features=5, bias=True)
  (7): Linear(in_features=2464, out_features=5, bias=True)
  (8): Linear(in_features=2464, out_features=5, bias=True)
  (9): Linear(in_features=2464, out_features=5, bias=True)
  (10): Linear(in_features=2464, out_features=5, bias=True)
  (11): Linear(in_features=2464, out_features=5, bias=True)
  (12): Linear(in_features=2464, out_features=5, bias=True)
  (13): Linear(in_features=2464, out_features=5, bias=True)
  (14): Linear(in_features=2464, out_features=5, bias=True)
  (15): Linear(in_features=2464, out_features=5, bias=True)
  (16): Linear(in_features=2464, 

RuntimeError: The size of tensor a (19129) must match the size of tensor b (2464) at non-singleton dimension 1

In [32]:
mod.numParams()

'EncParams: 83600, NeckParams: 4020, DecParams: 115855, || ModelParams: 287075 '

In [33]:
from torchinfo import summary

summary(mod)

Layer (type:depth-idx)                        Param #
TransformerAE                                 --
├─EncoderNeuronGroup: 1-1                     --
│    └─EmbedderNeuronGroup: 2-1               --
│    │    └─Linear: 3-1                       1,700
│    │    └─Linear: 3-2                       600
│    └─PositionalEncoder: 2-2                 --
│    └─ModuleList: 2-3                        --
│    │    └─EncoderLayer: 3-3                 81,100
│    └─Norm: 2-4                              200
├─EncoderNeuronGroup: 1-2                     --
│    └─EmbedderNeuronGroup: 2-5               --
│    │    └─Linear: 3-4                       1,700
│    │    └─Linear: 3-5                       600
│    └─PositionalEncoder: 2-6                 --
│    └─ModuleList: 2-7                        --
│    │    └─EncoderLayer: 3-6                 81,100
│    └─Norm: 2-8                              200
├─DecoderNeuronGroup: 1-3                     --
│    └─Neck2Seq: 2-9                          

In [54]:
#vec1.size(),len(out)

In [70]:
out[0].shape

torch.Size([1, 100])

In [71]:
out[1].shape

torch.Size([1, 700])

In [72]:
out[2][0].shape

torch.Size([1, 1, 9, 9])

In [73]:
out[3][0].shape

torch.Size([1, 1, 9, 9])

In [19]:
#DataLoader(dataset, batch_size=1)

In [19]:
criterion = nn.L1Loss()
optimizer = Adam(mod.parameters(), lr=0.0005)
scheduler = torch.optim.lr_scheduler.CyclicLR(optimizer, base_lr=1e-5, max_lr=0.0005, step_size_up=200, mode="triangular2", cycle_momentum=False)

In [20]:
num_epochs=40
L=[]
for epoch in tqdm(range(num_epochs)):
    for mul in range(len(train_pair)//30):
        cs=CustomDataset(train_pair,mul*30,min((mul+1)*30,len(train_pair)))
        for x1,x2,tg,labels in DataLoader(cs):
            x1=x1.to(torch.float32)
            x2=x2.to(torch.float32)
            x1=x1.to(device)
            x2=x2.to(device)
            
            mod.train()
            optimizer.zero_grad()
            output = mod(x1,x2)
            
            print(labels[0],x1.shape,tg.shape,output[0].shape)
            loss = criterion(output[0],tg)
            loss.backward()
            optimizer.step()
            L.append(loss.item())
            scheduler.step()


  0%|                                                    | 0/40 [00:00<?, ?it/s]
0it [00:00, ?it/s]
30it [00:00, 281.69it/s]
  0%|                                                    | 0/40 [00:02<?, ?it/s]


RuntimeError: The size of tensor a (220) must match the size of tensor b (9) at non-singleton dimension 1

In [69]:
vec.shape

torch.Size([2464, 100])

In [70]:
output[0].shape

torch.Size([2464, 100])

In [71]:
L

[1.2396024465560913,
 1.0457099676132202,
 0.805755615234375,
 0.6909157633781433,
 0.644996702671051,
 0.5092469453811646,
 0.40192678570747375,
 0.41317084431648254,
 0.38911423087120056,
 0.34021806716918945,
 0.3183385133743286,
 0.31227970123291016,
 0.30621036887168884,
 0.30430808663368225,
 0.2914847135543823,
 0.2810634970664978,
 0.2788929045200348,
 0.2815757989883423,
 0.2812448740005493,
 0.27170753479003906,
 0.26503410935401917,
 0.2678225636482239,
 0.27099722623825073,
 0.26777389645576477,
 0.26167818903923035,
 0.2599179148674011,
 0.26291796565055847,
 0.26350024342536926,
 0.2595277726650238,
 0.256998211145401,
 0.2578462064266205,
 0.25897300243377686,
 0.25773730874061584,
 0.2552947700023651,
 0.25501370429992676,
 0.2560119330883026,
 0.2556571066379547,
 0.2541976869106293,
 0.2534668743610382,
 0.25410860776901245]

# reconstruct Checkpoint

In [ ]:
from collections import OrderedDict
import copy
import numpy as np

for class_order_idx in range(len(ListExperiences)):
    for i in product(L_activations,L_inits):
        checkpoint=OrderedDict()
        vector_aux= copy.deepcopy(y)
        vector_aux=vector_aux.cpu()
        checkpoint["module_list.0.weight"]=torch.tensor(np.array(vector_aux[l][0:200]).reshape([8, 1, 5, 5]))
        checkpoint["module_list.0.bias"]=torch.tensor(np.array(vector_aux[l][200:208]).reshape([8]))
        checkpoint["module_list.3.weight"]=torch.tensor(np.array(vector_aux[l][208:1408]).reshape([6, 8, 5, 5]))
        checkpoint["module_list.3.bias"]=torch.tensor(np.array(vector_aux[l][1408:1414]).reshape([6]))
        checkpoint["module_list.6.weight"]=torch.tensor(np.array(vector_aux[l][1414:1510]).reshape([4, 6, 2, 2]))
        checkpoint["module_list.6.bias"]=torch.tensor(np.array(vector_aux[l][1510:1514]).reshape([4]))
        checkpoint["module_list.9.weight"]=torch.tensor(np.array(vector_aux[l][1514:2234]).reshape([20,36]))
        checkpoint["module_list.9.bias"]=torch.tensor(np.array(vector_aux[l][2234:2254]).reshape([20]))
        checkpoint["module_list.11.weight"]=torch.tensor(np.array(vector_aux[l][2254:2454]).reshape([10,20]))
        checkpoint["module_list.11.bias"]=torch.tensor(np.array(vector_aux[l][2454:2464]).reshape([10]))
        model = CNN(1,list(i)[0],0,list(i)[1]) ####
        model.load_state_dict(checkpoint)
        model.eval()
        torch.save(model.state_dict(), './checkpoints/Cumulative/{}/{}/{}/1/Reconsturcted checkpoint.pth'.format(ListExperiences[class_order_idx][:5],list(i)[0],list(i)[1]))

In [ ]:
preds